In [1]:
import csv
from collections import defaultdict

def build_inverted_indexes(file_path):
    index_title = defaultdict(list)
    index_author = defaultdict(list)
    index_category = defaultdict(list)
    books = {}

    try:
        with open(file_path, mode='r', encoding='utf-8') as file:
            reader = csv.reader(file)
            for row in reader:
                if len(row) != 5:
                    continue  # Hatalı satırları atla
                book_id, title, author, category, year = [x.strip() for x in row]
                books[book_id] = (title, author, category, year)

                # Harf duyarsız indeksleme
                index_title[title.lower()].append(book_id)
                index_author[author.lower()].append(book_id)
                index_category[category.lower()].append(book_id)

    except FileNotFoundError:
        print(f"Error: File not found at {file_path}")
    except Exception as e:
        print(f"Unexpected error: {e}")

    return books, index_title, index_author, index_category

def search(index, keyword, books):
    keyword = keyword.lower()  # Arama da küçük harfle yapılır
    results = index.get(keyword, [])
    if not results:
        print("No results found.")
        return
    for book_id in results:
        title, author, category, year = books[book_id]
        print(f"[{book_id}] {title} | {author} | {category} | {year}")

if __name__ == "__main__":

    file_path = "books_dataset.txt"  # 1 milyonluk dosya burada
    books, index_title, index_author, index_category = build_inverted_indexes(file_path)

    if not books:
        print("No books were loaded. Exiting.")
    else:
        print("Search by:\n1. Title\n2. Author\n3. Category")
        choice = input("Enter choice number: ").strip()
        keyword = input("Enter keyword: ").strip()

        if choice == "1":
            search(index_title, keyword, books)
        elif choice == "2":
            search(index_author, keyword, books)
        elif choice == "3":
            search(index_category, keyword, books)
        else:
            print("Invalid choice.")


Search by:
1. Title
2. Author
3. Category
Invalid choice.


In [ ]:
import csv
from collections import defaultdict
import tkinter as tk
from tkinter import ttk, messagebox

def build_inverted_indexes(file_path):
    index_title = defaultdict(list)
    index_author = defaultdict(list)
    index_category = defaultdict(list)
    books = {}

    try:
        with open(file_path, mode='r', encoding='utf-8') as file:
            reader = csv.reader(file)
            for row in reader:
                if len(row) != 5:
                    continue  # Hatalı satırları atla
                book_id, title, author, category, year = [x.strip() for x in row]
                books[book_id] = (title, author, category, year)

                # Harf duyarsız indeksleme
                index_title[title.lower()].append(book_id)
                index_author[author.lower()].append(book_id)
                index_category[category.lower()].append(book_id)

    except FileNotFoundError:
        messagebox.showerror("Hata", f"Dosya bulunamadı: {file_path}")
    except Exception as e:
        messagebox.showerror("Hata", f"Beklenmedik hata: {e}")

    return books, index_title, index_author, index_category

def search(index, keyword, books):
    keyword = keyword.lower()
    results = index.get(keyword, [])
    if not results:
        return ["Sonuç bulunamadı."]
    output = []
    for book_id in results:
        title, author, category, year = books[book_id]
        output.append(f"[{book_id}] {title} | {author} | {category} | {year}")
    return output

def on_search():
    search_type = search_type_var.get()
    keyword = keyword_entry.get().strip()

    if not keyword:
        messagebox.showwarning("Uyarı", "Lütfen bir anahtar kelime girin.")
        return

    if search_type == "Title":
        results = search(index_title, keyword, books)
    elif search_type == "Author":
        results = search(index_author, keyword, books)
    elif search_type == "Category":
        results = search(index_category, keyword, books)
    else:
        results = ["Geçersiz arama türü."]

    result_text.delete(1.0, tk.END)
    for line in results:
        result_text.insert(tk.END, line + "\n")

# Ana program
file_path = "books_dataset.txt"
books, index_title, index_author, index_category = build_inverted_indexes(file_path)

# GUI
root = tk.Tk()
root.title("Kitap Arama Arayüzü")
root.geometry("600x400")

tk.Label(root, text="Arama Türü:").pack(pady=5)
search_type_var = tk.StringVar(value="Title")
search_type_menu = ttk.Combobox(root, textvariable=search_type_var, values=["Title", "Author", "Category"])
search_type_menu.pack()

tk.Label(root, text="Anahtar Kelime:").pack(pady=5)
keyword_entry = tk.Entry(root, width=50)
keyword_entry.pack()

search_button = tk.Button(root, text="Ara", command=on_search)
search_button.pack(pady=10)

result_text = tk.Text(root, wrap=tk.WORD, height=15)
result_text.pack(padx=10, pady=10, fill=tk.BOTH, expand=True)

root.mainloop()


Search by:
1. Title
2. Author
3. Category
[4] A Tale of Two Cities | Fyodor Dostoyevsky | Horror | 2017
[5] Lord of the Flies | J.K. Rowling | Horror | 1904
[9] The Grapes of Wrath | Nathaniel Hawthorne | Horror | 1991
[47] Madame Bovary | Anna Sewell | Horror | 1998
[50] The Wizard of Oz | Emily Brontë | Horror | 1930
[67] Ivanhoe | Nathaniel Hawthorne | Horror | 1916
[82] The Hunchback of Notre Dame | Emily Brontë | Horror | 2013
[100] The Return of the King | L.M. Montgomery | Horror | 1977
[102] David Copperfield | Anna Sewell | Horror | 1925
[112] The Red Badge of Courage | Stephen Crane | Horror | 1962
[160] Fahrenheit 451 | Arthur Conan Doyle | Horror | 1998
[187] The Prince and the Pauper | J.K. Rowling | Horror | 1950
[196] The Return of the King | James Joyce | Horror | 1988
[202] The Old Man and the Sea | Johanna Spyri | Horror | 1946
[214] The Prince and the Pauper | Nathaniel Hawthorne | Horror | 1924
[217] The Pilgrim's Progress | Frances Hodgson Burnett | Horror | 1913
[

In [ ]:
import csv
from sortedcontainers import SortedDict # type: ignore
import tkinter as tk
from tkinter import ttk, messagebox

# Her alan için ayrı B+ Tree tarzı indeks (SortedDict)
def build_field_based_indexes(file_path):
    books = {}
    index_title = SortedDict()
    index_author = SortedDict()
    index_category = SortedDict()

    try:
        with open(file_path, mode='r', encoding='utf-8') as file:
            reader = csv.reader(file)
            for row in reader:
                if len(row) != 5:
                    continue  # Hatalı satır
                book_id, title, author, category, year = [x.strip() for x in row]
                books[book_id] = (title, author, category, year)

                # Her alan için indeksleme
                title_key = title.lower()
                author_key = author.lower()
                category_key = category.lower()

                index_title.setdefault(title_key, []).append(book_id)
                index_author.setdefault(author_key, []).append(book_id)
                index_category.setdefault(category_key, []).append(book_id)

    except FileNotFoundError:
        messagebox.showerror("Hata", f"Dosya bulunamadı: {file_path}")
    except Exception as e:
        messagebox.showerror("Hata", f"Beklenmedik hata: {e}")

    return books, index_title, index_author, index_category

# B+ Tree tarzı arama (keyword ile başlayan tüm kayıtlar)
def bplus_search(index: SortedDict, keyword: str, books: dict):
    keyword = keyword.lower()
    results = []
    for key in index.irange(keyword, keyword + 'z'):
        if key.startswith(keyword):
            for book_id in index[key]:
                title, author, category, year = books[book_id]
                results.append(f"[{book_id}] {title} | {author} | {category} | {year}")
    return results or ["Sonuç bulunamadı."]

def on_search():
    search_type = search_type_var.get()
    keyword = keyword_entry.get().strip()

    if not keyword:
        messagebox.showwarning("Uyarı", "Lütfen bir anahtar kelime girin.")
        return

    if search_type == "Title":
        results = bplus_search(index_title, keyword, books)
    elif search_type == "Author":
        results = bplus_search(index_author, keyword, books)
    elif search_type == "Category":
        results = bplus_search(index_category, keyword, books)
    else:
        results = ["Geçersiz arama türü."]

    result_text.delete(1.0, tk.END)
    for line in results:
        result_text.insert(tk.END, line + "\n")

# Dosya yükle ve indeks oluştur
file_path = "books_dataset.txt"
books, index_title, index_author, index_category = build_field_based_indexes(file_path)

# GUI Başlat
root = tk.Tk()
root.title("Kitap Arama Arayüzü (B+ Tree Indexing)")
root.geometry("700x500")

tk.Label(root, text="Arama Türü:").pack(pady=5)
search_type_var = tk.StringVar(value="Title")
search_type_menu = ttk.Combobox(root, textvariable=search_type_var, values=["Title", "Author", "Category"])
search_type_menu.pack()

tk.Label(root, text="Anahtar Kelime:").pack(pady=5)
keyword_entry = tk.Entry(root, width=60)
keyword_entry.pack()

search_button = tk.Button(root, text="Ara", command=on_search)
search_button.pack(pady=10)

result_frame = tk.Frame(root)
result_frame.pack(fill=tk.BOTH, expand=True, padx=10, pady=10)

result_scrollbar = tk.Scrollbar(result_frame)
result_scrollbar.pack(side=tk.RIGHT, fill=tk.Y)

result_text = tk.Text(result_frame, wrap=tk.WORD, yscrollcommand=result_scrollbar.set)
result_text.pack(fill=tk.BOTH, expand=True)
result_scrollbar.config(command=result_text.yview)

root.mainloop()


In [14]:
import csv
from collections import defaultdict
import tkinter as tk
from tkinter import ttk, messagebox

def build_inverted_indexes(file_path):
    index_title = defaultdict(list)
    index_author = defaultdict(list)
    index_category = defaultdict(list)
    books = {}

    try:
        with open(file_path, mode='r', encoding='utf-8') as file:
            reader = csv.reader(file)
            for row in reader:
                if len(row) != 5:
                    continue  # Hatalı satırları atla
                book_id, title, author, category, year = [x.strip() for x in row]
                books[book_id] = (title, author, category, year)

                index_title[title.lower()].append(book_id)
                index_author[author.lower()].append(book_id)
                index_category[category.lower()].append(book_id)

    except FileNotFoundError:
        messagebox.showerror("Hata", f"Dosya bulunamadı: {file_path}")
    except Exception as e:
        messagebox.showerror("Hata", f"Beklenmedik hata: {e}")

    return books, index_title, index_author, index_category

def search(index, keyword, books):
    keyword = keyword.lower()
    results = index.get(keyword, [])
    if not results:
        return ["Sonuç bulunamadı."]
    output = []
    for book_id in results:
        title, author, category, year = books[book_id]
        output.append(f"[{book_id}] {title} | {author} | {category} | {year}")
    return output

def on_search():
    search_type = search_type_var.get()
    keyword = keyword_entry.get().strip()

    if not keyword:
        messagebox.showwarning("Uyarı", "Lütfen bir anahtar kelime girin.")
        return

    if search_type == "Title":
        results = search(index_title, keyword, books)
    elif search_type == "Author":
        results = search(index_author, keyword, books)
    elif search_type == "Category":
        results = search(index_category, keyword, books)
    else:
        results = ["Geçersiz arama türü."]

    result_text.delete(1.0, tk.END)
    for line in results:
        result_text.insert(tk.END, line + "\n")

# Ana program
file_path = "books_dataset.txt"
books, index_title, index_author, index_category = build_inverted_indexes(file_path)

# GUI
root = tk.Tk()
root.title("Kitap Arama Arayüzü")
root.geometry("600x400")

tk.Label(root, text="Arama Türü:").pack(pady=5)
search_type_var = tk.StringVar(value="Title")
search_type_menu = ttk.Combobox(root, textvariable=search_type_var, values=["Title", "Author", "Category"])
search_type_menu.pack()

tk.Label(root, text="Anahtar Kelime:").pack(pady=5)
keyword_entry = tk.Entry(root, width=60)
keyword_entry.pack()

# ENTER tuşu ile arama yap
keyword_entry.bind("<Return>", lambda event: on_search())

search_button = tk.Button(root, text="Ara", command=on_search)
search_button.pack(pady=10)


# Text ve Scrollbar'ı birlikte yerleştirmek için bir Frame
text_frame = tk.Frame(root)
text_frame.pack(padx=10, pady=10, fill=tk.BOTH, expand=True)

# Scrollbar oluştur
scrollbar = tk.Scrollbar(text_frame)
scrollbar.pack(side=tk.RIGHT, fill=tk.Y)

# Text alanı oluştur ve scrollbar'a bağla
result_text = tk.Text(text_frame, wrap=tk.WORD, yscrollcommand=scrollbar.set)
result_text.pack(side=tk.LEFT, fill=tk.BOTH, expand=True)
scrollbar.config(command=result_text.yview)

root.mainloop()
 
 